In [2]:
from keras.preprocessing.text import Tokenizer
import numpy as np
import pandas as pd
from keras import optimizers, regularizers
from keras.models import Sequential
from keras.layers import Dense, Dropout, LSTM, Flatten, GRU
from keras.preprocessing.sequence import pad_sequences
from keras.callbacks import ModelCheckpoint
from keras.utils import np_utils, to_categorical
from keras.layers import Embedding
from sklearn.model_selection import train_test_split
import pickle
import re
import operator
from tqdm import tqdm
import seaborn as sns
import matplotlib.pyplot as plt

In [2]:
"""
For blog post, use epochs:
-5
-25
-70
-80
-110
-140 THRU 150
"""

'\nFor blog post, use epochs:\n-5\n-25\n-70\n-80\n-110\n-140 THRU 150\n'

In [3]:
from google.colab import files
files.upload()

Saving corpus.pkl to corpus.pkl


{'corpus.pkl': b'\x80\x04\x95V\x00\x01\x00\x00\x00\x00\x00]\x94(X%\x07\x00\x00Hey, hey Bye bye bye Bye bye! Bye bye! I\'m doing this tonight You\'re probably gonna start a fight I know this can\'t be right Hey baby, come on I loved you endlessly And you weren\'t there for me So now it\'s time to leave And make it alone I know that I can\'t take no more It ain\'t no lie I wanna see you out that door Baby, bye bye bye (bye bye) Don\'t wanna be a fool for you Just another player in your game for two You may hate me but it ain\'t no lie Baby, bye bye bye (bye bye) Don\'t really wanna make it tough I just wanna tell you that I had enough Might sound crazy but it ain\'t no lie Baby, bye bye bye Just hit me with the truth Now, girl you\'re more than welcome to So give me one good reason Baby, come on I live for you and me And now I really come to see That life would be much better Once you\'re gone I know that I can\'t take no more It ain\'t no lie I wanna see you out that door Baby, bye bye 

Delete all non-alphabetic characters and split the single words. Tokens are for each song the set of words that it contains. 
Words are the words of a song in order for each song.
Lines are the lines for each song. Each line consists of seven subsequent words

In [7]:
corpus = pickle.load(open('corpus.pkl', 'rb'))
cleaned = [re.sub('[^a-zA-Z ]', '', song) for song in corpus]

cleaned = list(set(cleaned))
tokens = [song.split() for song in cleaned]

words = []
for song in cleaned:
    for word in song.split():
        words.append(word)

lines = []
for i in range(len(words)-7):
    lines.append(words[i:i+7])

In [9]:
lines_unique = []
for line in tqdm(lines):
    if line not in lines_unique:
        lines_unique.append(line)
len(lines_unique)

100%|██████████| 886320/886320 [3:19:39<00:00, 73.99it/s]


616278

In [11]:
pickle.dump(lines_unique, open('unique_lines.pkl', 'wb'))

In [3]:
infile = open('unique_lines.pkl','rb')
lines_unique = pickle.load(infile)

In [1]:
*10**10

SyntaxError: ignored

In [4]:
#Turn words to ints
tokenizer = Tokenizer()
tokenizer.fit_on_texts(lines_unique)
sequences = tokenizer.texts_to_sequences(lines_unique)
vocab_size = len(tokenizer.word_index) + 1

sequences = np.array(sequences)

In [6]:
sequences.shape

(616278, 7)

In [ ]:
X, y = sequences[:,:-1], sequences[:,-1]
y = to_categorical(y, num_classes=vocab_size)
seq_length = X.shape[1]

In [ ]:
#Create model *DONT USE DROPOUT - DEPENDENCY ERROR*
model = Sequential()
model.add(Embedding(vocab_size, output_dim=50, input_length=seq_length))
model.add(GRU(256, return_sequences=True))
model.add(GRU(256))
model.add(Dense(100, activation='relu'))
model.add(Dense(vocab_size, activation='softmax'))

In [ ]:
filepath = "models/weights.{epoch:02d}-{loss:.2f}-bigger.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor="loss", verbose=1, save_best_only=False, mode="min", period = 5)
callbacks_list = [checkpoint]

model.fit(X, y, batch_size=256, epochs=150, callbacks=callbacks_list)